BloomTech Data Science

*Unit 2, Sprint 3, Module 2*

---


# Wrangle ML datasets

- [ ] Continue to clean and explore your data.
- [ ] For the evaluation metric you chose, what score would you get just by guessing?
- [ ] Can you make a fast, first model that beats guessing?

**We recommend that you use your portfolio project dataset for all assignments this sprint.**

**But if you aren't ready yet, or you want more practice, then use the New York City property sales dataset for today's assignment.** Follow the instructions below, to just keep a subset for the Tribeca neighborhood, and remove outliers or dirty data. [Here's a video walkthrough](https://youtu.be/pPWFw8UtBVg?t=584) you can refer to if you get stuck or want hints!

- Data Source: [NYC OpenData: NYC Citywide Rolling Calendar Sales](https://data.cityofnewyork.us/dataset/NYC-Citywide-Rolling-Calendar-Sales/usep-8jbt)
- Glossary: [NYC Department of Finance: Rolling Sales Data](https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page)

In [2]:
%%capture
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://github.com/bloominstituteoftechnology/DS-Unit-2-Applied-Modeling/tree/master/data/'
    !pip install category_encoders==2.*
    !pip install ydata-profiling

# If you're working locally:
else:
    DATA_PATH = '../data/'

In [4]:
import pandas as pd
from sklearn.pipeline import make_pipeline
from sklearn.impute import SimpleImputer
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import classification_report, roc_curve, ConfusionMatrixDisplay, \
    RocCurveDisplay, roc_auc_score
import matplotlib.pyplot as plt
import pandas_profiling
import plotly.express as px
from sklearn.linear_model import LinearRegression
from ipywidgets import interact

<ipython-input-4-a161bd16e434>:10: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling` instead.
  import pandas_profiling


In [ ]:
# Read New York City property sales data
import pandas as pd
from ydata_profiling import ProfileReport
df = pd.read_csv(DATA_PATH+'condos/NYC_Citywide_Rolling_Calendar_Sales.csv')

In [5]:
df = pd.read_csv('https://raw.githubusercontent.com/bloominstituteoftechnology/DS-Unit-2-Applied-Modeling/master/data/condos/NYC_Citywide_Rolling_Calendar_Sales.csv')

Your code starts here:

In [6]:
# Change column names: replace spaces with underscores
df.columns = [col.replace(' ', '_') for col in df]

In [7]:
# Get Pandas Profiling Report
df.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [8]:
# Keep just the subset of data for the Tribeca neighborhood
# Check how many rows you have now. (Should go down from > 20k rows to 146)
mask = df['NEIGHBORHOOD'].str.contains('TRIBECA')
df[mask]

BOROUGH NEIGHBORHOOD          BUILDING_CLASS_CATEGORY  \
220          1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
763          1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
996          1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
1276         1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
1542         1      TRIBECA          02 TWO FAMILY DWELLINGS   
...        ...          ...                              ...   
22221        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
22732        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
22733        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
22897        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
22898        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   

      TAX_CLASS_AT_PRESENT  BLOCK   LOT  EASE-MENT BUILDING_CLASS_AT_PRESENT  \
220                      2    222  1013        NaN                        R4   
763                      2     16  9022        NaN                        R4   
996                      2    212  1404        NaN                        R4   
1276                     2     16  1441        NaN                        R4   
1542                     1    132    26        NaN                        S2   
...                    ...    ...   ...        ...                       ...   
22221                    2    222  1206        NaN                        R4   
22732                    2     16  1806        NaN                        R4   
22733                    2     16  8071        NaN                        R4   
22897                    2     16  8132        NaN                        R4   
22898                    2    140  1162        NaN                        R4   

                          ADDRESS APARTMENT_NUMBER  ...  RESIDENTIAL_UNITS  \
220         181 HUDSON STREET, 6D               6D  ...                1.0   
763    10 LITTLE WEST STREET, 19A              19A  ...                1.0   
996           11 BEACH STREET, 1D               1D  ...                1.0   
1276    30 LITTLE WEST STREET, 7G               7G  ...                1.0   
1542         75 WARREN STREET, XX              NaN  ...                2.0   
...                           ...              ...  ...                ...   
22221    443 GREENWICH STREET, 1F               1F  ...                1.0   
22732  70 LITTLE WEST STREET, 11K              11K  ...                1.0   
22733      2 SOUTH END AVENUE, 5G               5G  ...                1.0   
22897      2 SOUTH END AVENUE, 8B               8B  ...                1.0   
22898        311 GREENWICH ST, 8B               8B  ...                1.0   

       COMMERCIAL_UNITS  TOTAL_UNITS  LAND_SQUARE_FEET GROSS_SQUARE_FEET  \
220                 0.0          1.0             7,878            1840.0   
763                 0.0          1.0                 0            1759.0   
996                 0.0          1.0            11,213            2651.0   
1276                0.0          1.0                 0            1190.0   
1542                1.0          3.0             1,819           10117.0   
...                 ...          ...               ...               ...   
22221               0.0          1.0            35,127            2429.0   
22732               0.0          1.0                 0            1601.0   
22733               0.0          1.0                 0             634.0   
22897               0.0          1.0                 0             939.0   
22898               0.0          1.0             9,900             695.0   

       YEAR_BUILT  TAX_CLASS_AT_TIME_OF_SALE  BUILDING_CLASS_AT_TIME_OF_SALE  \
220        1909.0                          2                              R4   
763           0.0                          2                              R4   
996        1900.0                          2                              R4   
1276       2005.0                          2                              R4   
1542       1905.0          

In [9]:
# Keep this subset of Tribeca properties
df = df[mask]

# Down from > 20k rows to < 150
df.shape

(146, 21)

In [10]:
# Q. What's the date range of these property sales in Tribeca?
df['SALE_DATE'].describe()

count            146
unique            66
top       02/12/2019
freq              17
Name: SALE_DATE, dtype: object

In [11]:
# The Pandas Profiling Report showed that SALE_PRICE was read as strings
# Convert it to integers
df['SALE_DATE'] = pd.to_datetime(df['SALE_DATE'], infer_datetime_format=True)
df['SALE_DATE'].describe()

<ipython-input-11-d3c8e157e87e>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['SALE_DATE'] = pd.to_datetime(df['SALE_DATE'], infer_datetime_format=True)
<ipython-input-11-d3c8e157e87e>:4: FutureWarning: Treating datetime data as categorical rather than numeric in `.describe` is deprecated and will be removed in a future version of pandas. Specify `datetime_is_numeric=True` to silence this warning and adopt the future behavior now.
  df['SALE_DATE'].describe()


count                     146
unique                     66
top       2019-02-12 00:00:00
freq                       17
first     2019-01-03 00:00:00
last      2019-04-30 00:00:00
Name: SALE_DATE, dtype: object

In [13]:
df['SALE_PRICE'] = (
    df['SALE_PRICE']
    .str.replace('$', '')
    .str.replace('-', '')
    .str.replace(',', '')
    .astype(int)
)

AttributeError: Can only use .str accessor with string values!

In [14]:
pd.options.display.float_format = '{:,.0f}'.format
df.describe()

BOROUGH  BLOCK   LOT  EASE-MENT  ZIP_CODE  RESIDENTIAL_UNITS  \
count      146    146   146          0       146                146   
mean         1    123 1,980        NaN     9,732                  3   
std          0     84 1,738        NaN     1,843                 23   
min          1     16     1        NaN         0                  0   
25%          1     16 1,112        NaN    10,007                  1   
50%          1    142 1,362        NaN    10,013                  1   
75%          1    212 2,194        NaN    10,013                  1   
max          1    224 9,057        NaN    10,282                283   

       COMMERCIAL_UNITS  TOTAL_UNITS  GROSS_SQUARE_FEET  YEAR_BUILT  \
count               146          146                146         146   
mean                  0            3              4,574       1,595   
std                   0           24             25,521         781   
min                   0            0                  0           0   
25%                   0            1                862       1,905   
50%                   0            1              1,788       1,986   
75%                   0            1              2,522       2,006   
max                   4          286            305,542       2,016   

       TAX_CLASS_AT_TIME_OF_SALE  SALE_PRICE  
count                        146         146  
mean                           2   8,884,964  
std                            0  23,639,981  
min                            1           0  
25%                            2     976,875  
50%                            2   2,750,000  
75%                            2   7,131,025  
max                            4 260,000,000

In [15]:
# Q. What is the maximum SALE_PRICE in this dataset?
df.query('SALE_PRICE == 260000000')

BOROUGH NEIGHBORHOOD           BUILDING_CLASS_CATEGORY  \
6499        1      TRIBECA  08 RENTALS - ELEVATOR APARTMENTS   

     TAX_CLASS_AT_PRESENT  BLOCK  LOT  EASE-MENT BUILDING_CLASS_AT_PRESENT  \
6499                    2    224    1        NaN                        D8   

                   ADDRESS APARTMENT_NUMBER  ...  RESIDENTIAL_UNITS  \
6499  34 DESBROSSES STREET              NaN  ...                283   

      COMMERCIAL_UNITS  TOTAL_UNITS  LAND_SQUARE_FEET GROSS_SQUARE_FEET  \
6499                 3          286            36,858           305,542   

      YEAR_BUILT  TAX_CLASS_AT_TIME_OF_SALE  BUILDING_CLASS_AT_TIME_OF_SALE  \
6499       2,007                          2                              D8   

     SALE_PRICE  SALE_DATE  
6499  260000000 2019-02-01  

[1 rows x 21 columns]

In [16]:
# Look at the row with the max SALE_PRICE
df.query('SALE_PRICE == 260000000')

BOROUGH NEIGHBORHOOD           BUILDING_CLASS_CATEGORY  \
6499        1      TRIBECA  08 RENTALS - ELEVATOR APARTMENTS   

     TAX_CLASS_AT_PRESENT  BLOCK  LOT  EASE-MENT BUILDING_CLASS_AT_PRESENT  \
6499                    2    224    1        NaN                        D8   

                   ADDRESS APARTMENT_NUMBER  ...  RESIDENTIAL_UNITS  \
6499  34 DESBROSSES STREET              NaN  ...                283   

      COMMERCIAL_UNITS  TOTAL_UNITS  LAND_SQUARE_FEET GROSS_SQUARE_FEET  \
6499                 3          286            36,858           305,542   

      YEAR_BUILT  TAX_CLASS_AT_TIME_OF_SALE  BUILDING_CLASS_AT_TIME_OF_SALE  \
6499       2,007                          2                              D8   

     SALE_PRICE  SALE_DATE  
6499  260000000 2019-02-01  

[1 rows x 21 columns]

In [17]:
# Get value counts of TOTAL_UNITS
# Q. How many property sales were for multiple units?
df['TOTAL_UNITS'].value_counts()

1      131
0       11
3        1
8        1
286      1
5        1
Name: TOTAL_UNITS, dtype: int64

In [18]:
# Keep only the single units
df.query('TOTAL_UNITS==1')
df.describe()

BOROUGH  BLOCK   LOT  EASE-MENT  ZIP_CODE  RESIDENTIAL_UNITS  \
count      146    146   146          0       146                146   
mean         1    123 1,980        NaN     9,732                  3   
std          0     84 1,738        NaN     1,843                 23   
min          1     16     1        NaN         0                  0   
25%          1     16 1,112        NaN    10,007                  1   
50%          1    142 1,362        NaN    10,013                  1   
75%          1    212 2,194        NaN    10,013                  1   
max          1    224 9,057        NaN    10,282                283   

       COMMERCIAL_UNITS  TOTAL_UNITS  GROSS_SQUARE_FEET  YEAR_BUILT  \
count               146          146                146         146   
mean                  0            3              4,574       1,595   
std                   0           24             25,521         781   
min                   0            0                  0           0   
25%                   0            1                862       1,905   
50%                   0            1              1,788       1,986   
75%                   0            1              2,522       2,006   
max                   4          286            305,542       2,016   

       TAX_CLASS_AT_TIME_OF_SALE  SALE_PRICE  
count                        146         146  
mean                           2   8,884,964  
std                            0  23,639,981  
min                            1           0  
25%                            2     976,875  
50%                            2   2,750,000  
75%                            2   7,131,025  
max                            4 260,000,000

In [19]:
# Q. Now what is the max sales price? How many square feet does it have?
df.query('SALE_PRICE == 39285000')

BOROUGH NEIGHBORHOOD          BUILDING_CLASS_CATEGORY  \
9236        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   

     TAX_CLASS_AT_PRESENT  BLOCK   LOT  EASE-MENT BUILDING_CLASS_AT_PRESENT  \
9236                    2    223  1144        NaN                        R4   

                    ADDRESS APARTMENT_NUMBER  ...  RESIDENTIAL_UNITS  \
9236  70 VESTRY STREET, 12S              12S  ...                  1   

      COMMERCIAL_UNITS  TOTAL_UNITS  LAND_SQUARE_FEET GROSS_SQUARE_FEET  \
9236                 0            1                 0             8,346   

      YEAR_BUILT  TAX_CLASS_AT_TIME_OF_SALE  BUILDING_CLASS_AT_TIME_OF_SALE  \
9236       2,016                          2                              R4   

     SALE_PRICE  SALE_DATE  
9236   39285000 2019-02-15  

[1 rows x 21 columns]

In [20]:
# Q. How often did $0 sales occur in this subset of the data?

# There's a glossary here:
# https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page

# It says:
# A $0 sale indicates that there was a transfer of ownership without a
# cash consideration. There can be a number of reasons for a $0 sale including
# transfers of ownership from parents to children.

df.query('SALE_PRICE == 0')

BOROUGH NEIGHBORHOOD          BUILDING_CLASS_CATEGORY  \
996          1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
2987         1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
6095         1      TRIBECA   10 COOPS - ELEVATOR APARTMENTS   
6757         1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
7261         1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
7786         1      TRIBECA   10 COOPS - ELEVATOR APARTMENTS   
8095         1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8368         1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8641         1      TRIBECA   07 RENTALS - WALKUP APARTMENTS   
9921         1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
11327        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
12367        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
13950        1      TRIBECA                   17 CONDO COOPS   
16221        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
16222        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
18197        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
19751        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
20254        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
20502        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   

      TAX_CLASS_AT_PRESENT  BLOCK   LOT  EASE-MENT BUILDING_CLASS_AT_PRESENT  \
996                      2    212  1404        NaN                        R4   
2987                     2     16  3064        NaN                        R4   
6095                    2C    143     8        NaN                        D4   
6757                     2     16  2483        NaN                        R4   
7261                     2    217  1032        NaN                        R4   
7786                     2    179    17        NaN                        D0   
8095                     2    212  1017        NaN                        R4   
8368                     2     84  1150        NaN                        R4   
8641                    2A    193    38        NaN                        C4   
9921                     2     16  5468        NaN                        R4   
11327                    2    141  1069        NaN                        R4   
12367                    2     16  1519        NaN                        R4   
13950                    2    189  1006        NaN                        R9   
16221                    2     16  1119        NaN                        R4   
16222                    2     16  5175        NaN                        R4   
18197                    2     16  2309        NaN                        R4   
19751                    2     16  3690        NaN                        R4   
20254                    2    188  1133        NaN                        R4   
20502                    2     16  9057        NaN                        R4   

                          ADDRESS APARTMENT_NUMBER  ...  RESIDENTIAL_UNITS  \
996           11 BEACH STREET, 1D               1D  ...                  1   
2987         280 RECTOR PLACE, 6B               6B  ...                  1   
6095          171 DUANE STREET, 5              NaN  ...                  0   
6757        300 ALBANY STREET, 8E               8E  ...                  1   
7261         79 LAIGHT STREET, 6D               6D  ...                  1   
7786         90 HUDSON STREET, 6D              NaN  ...                  0   
8095        260 WEST BROADWAY, 5D               5D  ...                  1   
8368         140 WEST STREET, 25D              25D  ...                  1   
8641             59 WALKER STREET              NaN  ...                  4   
9921        200 RECTOR PLACE, 20N              20N  ...                  1   
11327        166 DUANE STREET, 7C               7C  ...                  1   
12367  30 LITTLE WEST STREET, 20A              20A  ...                  1   
13950         6 VARICK STREET, 9C              NaN  ...                  0   
16221       377 RECTOR PLACE, 20E

In [21]:
# Look at property sales for > 5,000 square feet
# Q. What is the highest square footage you see?
df.query('GROSS_SQUARE_FEET > 5000')

BOROUGH NEIGHBORHOOD            BUILDING_CLASS_CATEGORY  \
1542         1      TRIBECA            02 TWO FAMILY DWELLINGS   
4002         1      TRIBECA   08 RENTALS - ELEVATOR APARTMENTS   
6499         1      TRIBECA   08 RENTALS - ELEVATOR APARTMENTS   
8641         1      TRIBECA     07 RENTALS - WALKUP APARTMENTS   
9236         1      TRIBECA    13 CONDOS - ELEVATOR APARTMENTS   
10487        1      TRIBECA  15 CONDOS - 2-10 UNIT RESIDENTIAL   
16008        1      TRIBECA  15 CONDOS - 2-10 UNIT RESIDENTIAL   

      TAX_CLASS_AT_PRESENT  BLOCK   LOT  EASE-MENT BUILDING_CLASS_AT_PRESENT  \
1542                     1    132    26        NaN                        S2   
4002                    2B    143    16        NaN                        D2   
6499                     2    224     1        NaN                        D8   
8641                    2A    193    38        NaN                        C4   
9236                     2    223  1144        NaN                        R4   
10487                   2C    179  1607        NaN                        R1   
16008                   2C    179  1602        NaN                        R1   

                     ADDRESS APARTMENT_NUMBER  ...  RESIDENTIAL_UNITS  \
1542    75 WARREN STREET, XX              NaN  ...                  2   
4002    325 GREENWICH STREET              NaN  ...                  4   
6499    34 DESBROSSES STREET              NaN  ...                283   
8641        59 WALKER STREET              NaN  ...                  4   
9236   70 VESTRY STREET, 12S              12S  ...                  1   
10487    24 LEONARD ST, PH W             PH W  ...                  1   
16008   24 LEONARD STREET, 2                2  ...                  1   

       COMMERCIAL_UNITS  TOTAL_UNITS  LAND_SQUARE_FEET GROSS_SQUARE_FEET  \
1542                  1            3             1,819            10,117   
4002                  4            8             2,000            11,726   
6499                  3          286            36,858           305,542   
8641                  1            5             2,479            10,311   
9236                  0            1                 0             8,346   
10487                 0            1             9,983            39,567   
16008                 0            1             9,983            39,567   

       YEAR_BUILT  TAX_CLASS_AT_TIME_OF_SALE  BUILDING_CLASS_AT_TIME_OF_SALE  \
1542        1,905                          1                              S2   
4002        1,920                          2                              D2   
6499        2,007                          2                              D8   
8641        1,910                          2                              C4   
9236        2,016                          2                              R4   
10487       1,940                          2                              R1   
16008       1,940                          2                              R1   

      SALE_PRICE  SALE_DATE  
1542    12950000 2019-01-10  
4002     7300000 2019-01-23  
6499   260000000 2019-02-01  
8641           0 2019-02-13  
9236    39285000 2019-02-15  
10487    9857100 2019-02-22  
16008    9718000 2019-03-21  

[7 rows x 21 columns]

In [22]:
# What are the building class categories?
# How frequently does each occur?
df['BUILDING_CLASS_CATEGORY'].value_counts()

13 CONDOS - ELEVATOR APARTMENTS               121
10 COOPS - ELEVATOR APARTMENTS                  9
15 CONDOS - 2-10 UNIT RESIDENTIAL               8
08 RENTALS - ELEVATOR APARTMENTS                2
17 CONDO COOPS                                  2
02 TWO FAMILY DWELLINGS                         1
07 RENTALS - WALKUP APARTMENTS                  1
16 CONDOS - 2-10 UNIT WITH COMMERCIAL UNIT      1
46 CONDO STORE BUILDINGS                        1
Name: BUILDING_CLASS_CATEGORY, dtype: int64

In [23]:
# Keep subset of rows:
# Sale price more than $0,
# Building class category = Condos - Elevator Apartments

mask = (df['SALE_PRICE'] > 0) & (df['BUILDING_CLASS_CATEGORY'] == '13 CONDOS - ELEVATOR APARTMENTS')
df = df[mask]

# Check how many rows you have now. (Should be 106 rows.)
df.shape

(106, 21)

In [24]:
# Make a Plotly Express scatter plot of GROSS_SQUARE_FEET vs SALE_PRICE
px.scatter(df, x='GROSS_SQUARE_FEET', y='SALE_PRICE')

In [25]:
# Add an OLS (Ordinary Least Squares) trendline,
# to see how the outliers influence the "line of best fit"
px.scatter(df, x='GROSS_SQUARE_FEET', y='SALE_PRICE', trendline='ols')

In [26]:
# Look at sales for more than $35 million

# All are at 70 Vestry Street
# All but one have the same SALE_PRICE & SALE_DATE
# Was the SALE_PRICE for each? Or in total?
# Is this dirty data?

df.query('SALE_PRICE > 35000000')

BOROUGH NEIGHBORHOOD          BUILDING_CLASS_CATEGORY  \
8370        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8371        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8372        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8373        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8374        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8375        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8376        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8377        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8378        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8379        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8380        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8381        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8382        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8383        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
8384        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   
9236        1      TRIBECA  13 CONDOS - ELEVATOR APARTMENTS   

     TAX_CLASS_AT_PRESENT  BLOCK   LOT  EASE-MENT BUILDING_CLASS_AT_PRESENT  \
8370                    2    223  1105        NaN                        R4   
8371                    2    223  1123        NaN                        R4   
8372                    2    223  1124        NaN                        R4   
8373                    2    223  1125        NaN                        R4   
8374                    2    223  1126        NaN                        R4   
8375                    2    223  1127        NaN                        R4   
8376                    2    223  1128        NaN                        R4   
8377                    2    223  1129        NaN                        R4   
8378                    2    223  1130        NaN                        R4   
8379                    2    223  1131        NaN                        R4   
8380                    2    223  1132        NaN                        R4   
8381                    2    223  1134        NaN                        R4   
8382                    2    223  1137        NaN                        R4   
8383                    2    223  1140        NaN                        R4   
8384                    2    223  1143        NaN                        R4   
9236                    2    223  1144        NaN                        R4   

                    ADDRESS APARTMENT_NUMBER  ...  RESIDENTIAL_UNITS  \
8370   70 VESTRY STREET, 3C               3C  ...                  1   
8371   70 VESTRY STREET, 6C               6C  ...                  1   
8372   70 VESTRY STREET, 6D               6D  ...                  1   
8373   70 VESTRY STREET, 6E               6E  ...                  1   
8374   70 VESTRY STREET, 6F               6F  ...                  1   
8375   70 VESTRY STREET, 7A               7A  ...                  1   
8376   70 VESTRY STREET, 7B               7B  ...                  1   
8377   70 VESTRY STREET, 7C               7C  ...                  1   
8378   70 VESTRY STREET, 7D               7D  ...                  1   
8379   70 VESTRY STREET, 7E               7E  ...                  1   
8380   70 VESTRY STREET, 7F               7F  ...                  1   
8381   70 VESTRY STREET, 8W               8W  ...                  1   
8382   70 VESTRY STREET, 9W               9W  ...                  1   
8383  70 VESTRY STREET, 10W              10W  ...                  1   
8384  70 VESTRY STREET, 11W              11W  ...                  1   
9236  70 VESTRY STREET, 12S              12S  ...                  1   

      COMMERCIAL_UNITS  TOTAL_UNITS  LAND_SQUARE_FEET GROSS_SQUARE_FEET  \
8370                 0            1                 0             1,670   
8371                 0            1                 0             1,906   
8372                 0            1                 0             2,536   
8373                 0            1                 0            

In [27]:
# Make a judgment call:
# Keep rows where sale price was < $35 million
df = df.query('SALE_PRICE < 35000000')

# Check how many rows you have now. (Should be down to 90 rows.)
df.shape

(90, 21)

In [28]:
# Now that you've removed outliers,
# Look again at a scatter plot with OLS (Ordinary Least Squares) trendline
px.scatter(df, x='GROSS_SQUARE_FEET', y= 'SALE_PRICE', trendline='ols')